In [ ]:
import numpy as np
from scipy import signal
import matplotlib.pyplot as plt
import pandas as pd
from scipy.fft import fft, fftfreq

## Filter comparison

In [ ]:
alpha = 0.01
mavg_b = [alpha]
mavg_a = [1, -(1-alpha)]

In [ ]:
# Sinc filter
b_sinc = [
    0.013166773445594984,
    0.015510026576574206,
    0.017943762856303655,
    0.020436419999452039,
    0.022953654956480787,
    0.025459023223972144,
    0.027914730737546672,
    0.030282439536854874,
    0.032524106530629059,
    0.034602833419516990,
    0.036483705201686277,
    0.038134594717421900,
    0.039526911389630152,
    0.040636273671486346,
    0.041443086683647982,
    0.041933009054862178,
    0.042097295996679322,
    0.041933009054862178,
    0.041443086683647982,
    0.040636273671486346,
    0.039526911389630152,
    0.038134594717421900,
    0.036483705201686277,
    0.034602833419516990,
    0.032524106530629059,
    0.030282439536854874,
    0.027914730737546672,
    0.025459023223972144,
    0.022953654956480787,
    0.020436419999452039,
    0.017943762856303655,
    0.015510026576574206,
    0.013166773445594984,
]
b_sinc = [
    -0.000005301919181359,
    -0.000020372384569462,
    -0.000043393375246200,
    -0.000071643508460196,
    -0.000101272447699964,
    -0.000127045709202358,
    -0.000142084479366378,
    -0.000137630058679112,
    -0.000102865422361326,
    -0.000024826753571648,
    0.000111564545505229,
    0.000323323938002668,
    0.000629062120588115,
    0.001048471626315150,
    0.001601644955843253,
    0.002308239744151386,
    0.003186518744650963,
    0.004252303894058680,
    0.005517893567100900,
    0.006990999568786174,
    0.008673764799041549,
    0.010561923390649710,
    0.012644162210467481,
    0.014901735907231652,
    0.017308377414832196,
    0.019830532444994709,
    0.022427930710902887,
    0.025054489273884574,
    0.027659525485854094,
    0.030189239563895277,
    0.032588410933658420,
    0.034802239101869442,
    0.036778249821351520,
    0.038468181363671021,
    0.039829764251821352,
    0.040828311002284692,
    0.041438040179150003,
    0.041643070995549647,
    0.041438040179150003,
    0.040828311002284692,
    0.039829764251821366,
    0.038468181363671021,
    0.036778249821351520,
    0.034802239101869456,
    0.032588410933658420,
    0.030189239563895291,
    0.027659525485854094,
    0.025054489273884584,
    0.022427930710902898,
    0.019830532444994709,
    0.017308377414832207,
    0.014901735907231647,
    0.012644162210467488,
    0.010561923390649715,
    0.008673764799041547,
    0.006990999568786178,
    0.005517893567100902,
    0.004252303894058680,
    0.003186518744650965,
    0.002308239744151388,
    0.001601644955843254,
    0.001048471626315152,
    0.000629062120588114,
    0.000323323938002668,
    0.000111564545505229,
    -0.000024826753571648,
    -0.000102865422361327,
    -0.000137630058679112,
    -0.000142084479366378,
    -0.000127045709202359,
    -0.000101272447699963,
    -0.000071643508460196,
    -0.000043393375246200,
    -0.000020372384569461,
    -0.000005301919181359,
]
b_sinc = np.around([k * 56536 for k in b_sinc])/65536


def combined_sinc_mavg(alpha = 0.4):
    b1 = [alpha]
    b2 = b_sinc
    a1 = [1, -(1-alpha)]
    a2 = [1]
    
    b = np.convolve(b1, b2)
    a = np.convolve(a1, a2)
    return b,a

def iir_notch(freq, r, fsa):
    b = [1, -2*np.cos(freq/fsa*2*np.pi), 1]
    a = [1, -2*r*np.cos(freq/fsa*2*np.pi), r*r]
    return b,a

In [ ]:
def plot_transfer_func(b, a, fsa = 1):
    omega, vals = signal.freqz(b, a, worN = 1024)
    plt.plot(omega/(2*np.pi)*fsa, abs(vals))
    
sample_rate = 1e3/6
plt.figure(figsize=(16,8))
plt.yscale('log')
plot_transfer_func(mavg_b, mavg_a, sample_rate)
plt.ylabel('|H(w)| [dB]')
plt.xlabel('Frequency [Hz]')

plot_transfer_func(b_sinc, [1], sample_rate)

# Combined filter
b,a = combined_sinc_mavg(alpha = 1)
b_notch, a_notch = iir_notch(50, 0.875, sample_rate)
b = np.convolve(b, b_notch)
a = np.convolve(a, a_notch)
plot_transfer_func(b,a, sample_rate)
plt.grid()

plt.legend(['MAVG a = 0.01', 'SINC', 'SINC+MAVG'])
plt.xlim(0, 70)
plt.show()

# Notch filters (Not used for implementation)

In [ ]:
plt.figure(figsize=(16,8))
plt.yscale('log')
a = [1]
b = [1, -2*np.cos(50/sample_rate*2*np.pi), 1]
plot_transfer_func(b,a, sample_rate)

b = [1, -2*np.cos(60/sample_rate*2*np.pi), 1]
plot_transfer_func(b,a, sample_rate)

r = 0.875
b,a = iir_notch(50, r, sample_rate)
plot_transfer_func(b,a, sample_rate)

b,a = iir_notch(60, r, sample_rate)
plot_transfer_func(b,a, sample_rate)
plt.xlim(40,70)
plt.legend(['FIR 50 Hz Notch', 'FIR 60 Hz', 'IIR 50Hz', 'IIR 60Hz'])
plt.show()

# Singal testing

In [ ]:
N = 30000
time = np.linspace(0, 1/sample_rate*N, N, endpoint=False)
sig = 10*signal.sawtooth(2*np.pi*0.2*time)+10 #+ 0.5 * np.sin(2*np.pi*50*time)+0.8 * np.sin(2*np.pi*80*time)

plt.figure(figsize=(16,8))

spur_len = 3

sig[1000:1000+spur_len] = sig[1000]+5
sig[2000:2000+spur_len] = sig[2000]-6
sig[3000:3000+spur_len] = sig[3000]+2
sig[4000:4000+spur_len] = sig[4000]+8


plt.plot(time, sig)


# Apply the combined filter:
b,a = combined_sinc_mavg(alpha = 1)

bn,an = iir_notch(50, 0.875, sample_rate)
a = np.convolve(a, an)
b = np.convolve(b, bn)

#b,a = mavg_b, mavg_a

w,h = signal.freqz(b,a)
gain_corr = round(1/abs(h[0])*65536)/65536

sig_f = signal.lfilter(b, a, sig) * gain_corr


print('Gain correction:', gain_corr)

plt.plot(time, sig_f)
plt.xlim(5,10)
plt.show()

plt.figure(figsize=(16,8))
plt.plot(time, abs(sig-sig_f))
plt.xlim(5,10)
plt.ylim(0,2)
plt.show()

In [ ]:

window = signal.windows.hamming(N)

h_sig = fft(sig*window)
f_sig = fftfreq(N, 1/sample_rate)[:N//2]

h_sig_f = fft(sig_f*window)
f_sig_f = fftfreq(N, 1/sample_rate)[:N//2]

plt.figure(figsize=(16,10))
plt.yscale('log')
plt.plot(f_sig, 2.0/N*abs(h_sig[0:N//2]))
plt.plot(f_sig_f, 2.0/N*abs(h_sig_f[0:N//2]))
plt.show();

# PT1000 HF Filtering

In [ ]:
raw_data = pd.read_csv(r'pt1000_hf_2kOhm_v1.3.dat')
raw_data = pd.read_csv(r'pt1000_hf_changing.dat')
time = np.linspace(0, 2000*6e-3, 2000, endpoint=False)

plt.figure(figsize=(22,12))
plt.plot(time, raw_data['hf_value']*2500/4096)

alpha = 0.005

mavg_b = [alpha]
mavg_a = [1, -(1-alpha)]

zi = signal.lfilter_zi(mavg_b, mavg_a)
filtered, _ = signal.lfilter(mavg_b, mavg_a, raw_data['hf_value'], zi=zi*raw_data['hf_value'][0])
plt.plot(time, filtered*2500/4096)
filtered_avg_low = filtered

alpha = 0.01
mavg_b = [alpha]
mavg_a = [1, -(1-alpha)]

zi = signal.lfilter_zi(mavg_b, mavg_a)
filtered, _ = signal.lfilter(mavg_b, mavg_a, raw_data['hf_value'], zi=zi*raw_data['hf_value'][0])
plt.plot(time, filtered*2500/4096)
filtered_avg = filtered



# Apply the combined filter:
b,a = combined_sinc_mavg(alpha = 0.08)

bn,an = iir_notch(4, 0.75, sample_rate)
a = np.convolve(a, an)
b = np.convolve(b, bn)

zi = signal.lfilter_zi(b, a)
filtered, _ = signal.lfilter(b, a, raw_data['hf_value'], zi=zi*raw_data['hf_value'][0])

w,h = signal.freqz(b,a)
gain_corr = round(1/abs(h[0])*65536)/65536

plt.plot(time, filtered*gain_corr*2500/4096)
plt.savefig('expl.pdf', format='pdf', dpi=1200)
plt.show()


## Spectrum

In [ ]:
window =signal.windows.hamming(len(raw_data['hf_value']))
raw_fft = fft(np.array(raw_data['hf_value'].to_list())*window)
f_raw = fftfreq(len(raw_data), 1/sample_rate)[:len(raw_data)//2]
plt.figure(figsize=(16,10));
plt.yscale('log')
plt.plot(f_raw, abs(raw_fft[:len(raw_data)//2]))

avg_fft = fft(np.array(filtered_avg)*window)
plt.plot(f_raw, abs(avg_fft[:len(raw_data)//2]))

avg_fft = fft(np.array(filtered_avg_low)*window)
plt.plot(f_raw, abs(avg_fft[:len(raw_data)//2]))

sinc_fft = fft(np.array(filtered)*window)
plt.plot(f_raw, abs(sinc_fft[:len(raw_data)//2]))
plt.xscale('log')
plt.show()

In [ ]:
print(np.std(filtered_avg_low/4096*2500))
print(np.std(filtered_avg/4096*2500))
print(np.std(filtered/4096*2500))

print('Min',min(filtered_avg/4096*2500), 'Max', max(filtered_avg)/4096*2500)
print('Min',min(filtered)/4096*2500*gain_corr, 'Max', max(filtered)/4096*2500*gain_corr)